In [16]:
from elasticsearch import Elasticsearch

In [17]:
es = Elasticsearch(
    "https://localhost:9200",
    basic_auth=("elastic","kmZd*ryHh-rkjiAu2Txw"),
    ca_certs="../http_ca.crt"
)
es.ping()

True

## Prepare the data

In [18]:
import pandas as pd

df = pd.read_csv("myntra_products_catalog.csv").loc[:499]
df.head()

ProductID                                        ProductName ProductBrand  \
0   10017413  DKNY Unisex Black & Grey Printed Medium Trolle...         DKNY   
1   10016283  EthnoVogue Women Beige & Grey Made to Measure ...   EthnoVogue   
2   10009781  SPYKAR Women Pink Alexa Super Skinny Fit High-...       SPYKAR   
3   10015921  Raymond Men Blue Self-Design Single-Breasted B...      Raymond   
4   10017833  Parx Men Brown & Off-White Slim Fit Printed Ca...         Parx   

   Gender  Price (INR)  NumImages  \
0  Unisex        11745          7   
1   Women         5810          7   
2   Women          899          7   
3     Men         5599          5   
4     Men          759          5   

                                         Description PrimaryColor  
0  Black and grey printed medium trolley bag, sec...        Black  
1  Beige & Grey made to measure kurta with churid...        Beige  
2  Pink coloured wash 5-pocket high-rise cropped ...         Pink  
3  Blue self-design bandhgala suitBlue self-desig...         Blue  
4  Brown and off-white printed casual shirt, has ...        White

In [19]:
df.isna().value_counts()

ProductID  ProductName  ProductBrand  Gender  Price (INR)  NumImages  Description  PrimaryColor
False      False        False         False   False        False      False        False           468
                                                                                   True             32
Name: count, dtype: int64

In [20]:
df.fillna("None", inplace=True)

## Convert the relevant field to Vector using BERT model

In [21]:
from sentence_transformers import SentenceTransformer
model = SentenceTransformer('all-mpnet-base-v2')

In [22]:
df["DescriptionVector"] = df["Description"].apply(lambda x: model.encode(x))

In [23]:
df.head()

ProductID                                        ProductName ProductBrand  \
0   10017413  DKNY Unisex Black & Grey Printed Medium Trolle...         DKNY   
1   10016283  EthnoVogue Women Beige & Grey Made to Measure ...   EthnoVogue   
2   10009781  SPYKAR Women Pink Alexa Super Skinny Fit High-...       SPYKAR   
3   10015921  Raymond Men Blue Self-Design Single-Breasted B...      Raymond   
4   10017833  Parx Men Brown & Off-White Slim Fit Printed Ca...         Parx   

   Gender  Price (INR)  NumImages  \
0  Unisex        11745          7   
1   Women         5810          7   
2   Women          899          7   
3     Men         5599          5   
4     Men          759          5   

                                         Description PrimaryColor  \
0  Black and grey printed medium trolley bag, sec...        Black   
1  Beige & Grey made to measure kurta with churid...        Beige   
2  Pink coloured wash 5-pocket high-rise cropped ...         Pink   
3  Blue self-design bandhgala suitBlue self-desig...         Blue   
4  Brown and off-white printed casual shirt, has ...        White   

                                   DescriptionVector  
0  [0.027645733, -0.002634167, -0.0035884373, 0.0...  
1  [-0.024660714, -0.028755445, -0.020332456, 0.0...  
2  [-0.04694328, 0.08182793, 0.048335195, -0.0001...  
3  [-0.01509876, -0.010285516, 0.009487349, -0.02...  
4  [-0.017746469, 0.006209531, 0.021813966, 0.026...

In [24]:
es.ping()

True

## Create new index in ElasticSearch!

In [25]:
from indexMapping import indexMapping

es.indices.create(index="all_products", mappings=indexMapping)

BadRequestError: BadRequestError(400, 'resource_already_exists_exception', 'index [all_products/iinrlACzQQC8Ik8LrQjRwg] already exists')

## Ingest the data into index

In [27]:
record_list = df.to_dict("records") #convert to json format

In [26]:
record_list

[{'ProductID': 10017413,
  'ProductName': 'DKNY Unisex Black & Grey Printed Medium Trolley Bag',
  'ProductBrand': 'DKNY',
  'Gender': 'Unisex',
  'Price (INR)': 11745,
  'NumImages': 7,
  'Description': 'Black and grey printed medium trolley bag, secured with a TSA lockOne handle on the top and one on the side, has a trolley with a retractable handle on the top and four corner mounted inline skate wheelsOne main zip compartment, zip lining, two compression straps with click clasps, one zip compartment on the flap with three zip pocketsWarranty: 5 yearsWarranty provided by Brand Owner / Manufacturer',
  'PrimaryColor': ' Black',
  'DescriptionVector': array([ 2.76457332e-02, -2.63416697e-03, -3.58843734e-03,  5.13587706e-02,
          3.09660453e-02,  1.40506886e-02,  7.27048656e-03,  3.13871652e-02,
         -6.23787604e-02, -3.82881449e-03,  3.15213948e-02,  7.55473375e-02,
          2.12643202e-03,  4.64894064e-02,  5.07448949e-02, -1.71942022e-02,
          1.22892447e-02, -1.95682

In [28]:
for record in record_list:
    try:
        es.index(index="all_products", document=record, id=record["ProductID"])
    except Exception as e:
        print(e)

In [29]:
es.count(index="all_products")

ObjectApiResponse({'count': 500, '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0}})

## Search the data

In [30]:
input_keyword = "Blue Shoes"
vector_of_input_keyword = model.encode(input_keyword)

query = {
    "field" : "DescriptionVector",
    "query_vector" : vector_of_input_keyword,
    "k" : 2,  # top 2 results
    "num_candidates" : 500,  # number of candidates to retrieve
}

res = es.knn_search(index="all_products", knn=query , source=["ProductName","Description"])
res["hits"]["hits"]

[{'_index': 'all_products',
  '_id': '10018013',
  '_score': 0.61429405,
  '_source': {'Description': 'A pair of round-toe blue sneakers, has regular styling, lace-up detailTextile upperCushioned footbedTextured and patterned outsoleWarranty: 3 monthsWarranty provided by brand/manufacturer',
   'ProductName': 'Puma Men Blue Sneakers'}},
 {'_index': 'all_products',
  '_id': '10018075',
  '_score': 0.61429405,
  '_source': {'Description': 'A pair of round-toe blue sneakers, has regular styling, lace-up detailTextile upperCushioned footbedTextured and patterned outsoleWarranty: 3 monthsWarranty provided by brand/manufacturer',
   'ProductName': 'Puma Men Blue Sneakers'}}]